In [ ]:
%matplotlib inline
# Another option is `%matplotlib widget`
import numpy as np, matplotlib as mpl, scipy as sp
from matplotlib import pylab, mlab, pyplot as plt
from matplotlib.pylab import plot, scatter, contour
from tqdm.notebook import tqdm, trange

from numpy import sqrt, pi, exp, log, floor, ceil, sin, cos
from numpy.linalg import norm

rng = np.random.default_rng()

## Graph a function

In [ ]:
xx = np.linspace( 0, .1, 1000 )
plot( xx, xx*sin(1/xx) )

## Compute π via a Monte Carlo method

In [ ]:
# Direct implementation (slow)
N = 10**6

n_inside = 0
for i in trange(N):
    U = rng.uniform( size=2 )
    if sqrt(U[0]**2 + U[1]**2) < 1:
        n_inside += 1

hat_π = 4*n_inside/N
print( f'π ≈ { hat_π:.4f}, error = {abs(pi-hat_π):.4f}' )

In [ ]:
%%time
# Use numpy functions
U = rng.uniform( size=(2, N) )
n_inside = np.sum( norm( U, axis=0 ) < 1 )

hat_π = 4*n_inside/N
print( f'π ≈ { hat_π:.4f}, error = {abs(pi-hat_π):.4f}' )

In [ ]:
plt.figure( figsize=(4,4) )

N = 10000
U = rng.uniform( size=(2, N) )
scatter( *U, s=.1, c=( norm(U, axis=0) < 1 ), cmap=plt.colormaps['coolwarm_r'] )

xx = np.linspace( 0, 1 )
y = sqrt( 1 - xx**2 )
plot( xx, y )
plt.fill_between( xx, y, alpha=.1 )

#plt.savefig( 'figures/intro-compute-pi.png', bbox_inches='tight', dpi=200 )

In [ ]:
# For large N, run in chunks.
N = 10**8
M = 1000
n_inside = 0
for i in trange(M):
    U = rng.uniform( size=(2, N//M) )
    n_inside += np.sum( norm( U, axis=0 ) < 1 )

hat_π = 4*n_inside/N
print( f'π ≈ { hat_π}, error = {abs(pi-hat_π)}' )

### Compute error as N increases

In [ ]:
M = 10**3 # Chunk size
n_iters = 1000
n_trials = 1000

hat_π = np.empty( (n_iters, n_trials) )
NN = np.arange( M, M*(1+n_iters), M )

for n in trange( n_iters ):
    U = rng.uniform( size=(2, M, n_trials) )
    n_inside = np.sum( norm( U, axis=0 ) < 1, axis=0 )
    hat_π[n] = 4*n_inside
hat_π = (np.cumsum( hat_π, axis=0 ).T / NN).T

In [ ]:
μ = hat_π.mean( axis=-1 )
σ = hat_π.std( axis=-1 )

plt.fill_between( NN, μ-σ, μ+σ, alpha=.3, label='Std Dev' )
for n in sorted( rng.choice( n_trials, replace=False, size=3) ):
    plot( NN, hat_π[:, n], alpha=.6, label=f'Trial {n+1}' )

plt.ylim( pi-.02, pi+.02)
plot( NN, μ, label='Average' )
plt.legend()
#plt.savefig( 'figures/intro-pi-error.png', bbox_inches='tight', dpi=200 )

In [ ]:
plt.loglog( NN, σ, label='σ' )

a = np.polyfit( log(NN), log(σ), 1 )
plt.loglog( NN, exp( a[0]*log(NN) + a[1] ), '--', alpha=.5, label=f'${exp(a[1]):.2f}\\, N^{{ {a[0]:.3f} }}$' )

_= plt.xlabel( 'log $N$' )
_ = plt.title( f'log log plot of σ vs $N$' )
plt.legend()
#plt.savefig( 'figures/intro-pi-std-decay.png', bbox_inches='tight', dpi=200 )

## Volume of a $d$-dimensional ball

In [ ]:
N = 10**6
D = 30
vol=np.empty(D)
hat_vol=np.empty_like(vol)

for d in trange( 1, D ):
    vol[d] = pi**(d/2) / sp.special.gamma( d/2 + 1 )

    U = rng.uniform( size=(d, N) )
    n_inside = np.sum( norm(U, axis=0) < 1 )
    hat_vol[d] = 2**d * n_inside/N

del U

In [ ]:
dd = np.arange( 1, D )
plot( dd, vol[1:], label='Exact' )
plot( dd, hat_vol[1:], label='Approximation' )
_ = plt.title( 'Volume of a $d$ dimensional ball' )
#plt.savefig( 'figures/intro-vol-ball.png', bbox_inches='tight', dpi=200 )

In [ ]:
hat_vol